In [5]:
import pandas as pd
import re 
import numpy as np
import matplotlib.pyplot as plt
import pymorphy2
from nltk.tokenize import word_tokenize
from nltk.tokenize.casual import TweetTokenizer
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestRegressor
from sklearn.model_selection import cross_val_score
from sklearn.model_selection import GridSearchCV
from sklearn.tree import DecisionTreeRegressor
from sklearn.ensemble import GradientBoostingRegressor
from sklearn import tree
from sklearn.tree import plot_tree

In [3]:
pip install pymorphy2

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 55.5/55.5 kB 6.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 8.2/8.2 MB 52.1 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Created wheel for docopt: filename=docopt-0.6.2-py2.py3-none-any.whl size=13721 sha256=781884699ede69409fe32db2534041a9c3cfe4b503f3cd862fe3b2bf7b100762
  Stored in directory: /root/.cache/pip/wheels/fc/ab/d4/5da2067ac95b36618c629a5f93f809425700506f72c9732fac
Successfully built docopt


In [4]:
pip install vk_api

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 48.6/48.6 kB 3.4 MB/s eta 0:00:00


#### Источники данных

In [58]:
token_vk = "vk1.a.tq8B09NkUg54oexVzZpbzAooNU2Pj2RoJcGlX_CrZZDEokJSBueXTKYfQ8WzJdmgX9xXdhR_OWvkqM4wRzGiq9c-GH0rDo-XSnpwto2yGNIMoDCM7mccKyAb92aVNvv3nSzQhQGLVFUP05r5hpVnrh4XkXoaifSkXxhoLWWuCayAkt1KYCAAOb4w1z2oYgpxv4IQC08faT03xGDSs8Ygsw"
id_auto = '-93614683'
mas_id = [id_auto]

#### Получение данных

In [60]:
from vk_api import VkApi
import vk_api

token = token_vk

def main(offset: int, token: str, group_id: str):
    vk = vk_api.VkApi(token=token) # авторизация через токен (желательно)
    api = vk.get_api()
    posts = api.wall.get(owner_id = group_id, offset = offset, count=100)['items']
    posts_strings = [post['text'] for post in posts]
    num_like = []
    comments_strings = []
    for post in posts:
        comments = api.wall.getComments(owner_id = group_id, post_id=post['id'], count=100)['items']
        comments_strings.append([comment['text'] for comment in comments])
        itemID = post['id']
        isLiked = api.likes.getList(
        type = 'post', 
        owner_id = group_id, 
        item_id = itemID               
        )
        num_like.append(isLiked['count'])
    return posts_strings, comments_strings, num_like


combo_list_posts = []
combolist_comments = []
combolist_like_count = []

for group_id in mas_id:
    for i in range(0, 1001, 100):
        try:
            rzd_posts, comments_strings_rzd, rzd_like_count = main(offset = i, token = token, group_id = group_id)
            combo_list_posts.extend(rzd_posts)
            combolist_comments.extend(comments_strings_rzd)
            combolist_like_count.extend(rzd_like_count)
            print(group_id,i)
        except:
            print('Постов больше нет на смещении: ', i)


-93614683 0
-93614683 100
-93614683 200
-93614683 300
-93614683 400
-93614683 500
-93614683 600
-93614683 700
-93614683 800
-93614683 900
-93614683 1000


In [61]:
len(combo_list_posts)

1100

In [71]:
#категории постов
mas_category=['автомобильный' for i in range(1100)]

In [65]:
#количество комментариев в каждом посту
combolist_comments_count = [len(comments) for comments in combolist_comments]

In [72]:
#датасет с данными
data = pd.DataFrame({'посты':combo_list_posts,'комментарии':combolist_comments_count,'лайки':combolist_like_count})

In [73]:
data

посты  комментарии  лайки
0     В Москве музей отреставрировал ранний ГАЗ-24-у...            7     84
1     Новый спортивный Урал дебютировал в трак-триал...            3     83
2     Глава думской фракции предложил создать «народ...           42     66
3     Hyundai Motor ждет разрешения на продажу завод...            1     19
4     АВТОВАЗ займет три простаивающие площадки выпу...            6     40
...                                                 ...          ...    ...
1095  Тут такое дело... Я опять про Яндекс и его бес...            4     36
1096  Как в Новосибирске затеяли новый автомобиль сд...            4     24
1097  Новую панель приборов Нивы (Лады 4х4) я видел ...           18     55
1098  Haval F7x: дважды кроссовер\n\nСнег пошел с са...            7     22
1099  НАМИ изготовил первый кабриолет Aurus для част...            4     55

[1100 rows x 3 columns]

#### EDA и инженерия данных

In [68]:
data = pd.read_csv('/content/submission.csv')

In [74]:
data=data.drop_duplicates()#удаление дубликатов

In [75]:
data.isnull().sum()#переменные с пропуском

посты          0
комментарии    0
лайки          0
dtype: int64

#### Токенизация

In [13]:
data

посты  комментарии  лайки
0    Хорошо, что у этих мужиков хорошая смекалка, т...           36    617
2    Делаем своими руками турбиновый двигатель. Отл...            0      3
3    Мужик красавчик, у него не только золотые руки...            0      6
5         Опасно, не надёжно, но это реально работает.            0      1
6                       Lada XRAY и о её безопасности.            0      0
..                                                 ...          ...    ...
394  Такой Оки вы ещё точно не видели. Получился ун...            3     68
395                  А что вы думаете по этому поводу?            2     11
396      А за какой автомобиль болели вы в этом гонке?            3      4
397               Блокируем колёса необычным способом.            4      6
398  Вот почему не стоит лезть в перёд фуры. Скорос...            1     12

[390 rows x 3 columns]

In [76]:
data = data.dropna()

In [77]:
data = data.astype({'посты': np.str})

<ipython-input-77-9bc2decd869f>:1: DeprecationWarning: `np.str` is a deprecated alias for the builtin `str`. To silence this warning, use `str` by itself. Doing this will not modify any behavior and is safe. If you specifically wanted the numpy scalar type, use `np.str_` here.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
  data = data.astype({'посты': np.str})


In [78]:
import nltk

In [79]:
nltk.download('stopwords')

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


True

In [80]:
nltk.download('wordnet')

[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


True

In [81]:
stop_words = stopwords.words('russian')
morph = pymorphy2.MorphAnalyzer()
lemmatizer = WordNetLemmatizer()
tknzr = TweetTokenizer()
tokenize_document = []

for document in data['посты']:
    document = re.sub(r"https?://[^,\s]+,?", "", document)
    document = re.sub('[0|1|2|3|4|5|6|7|8|9|/|\|.|,|:|;|#|$|%|№|@|<|>|?|!|-|)|(|«|»|"]', "", document)
    document = tknzr.tokenize(document)
    document = [word.lower() for word in document]
    document = [word for word in document if word not in stop_words]
    document = [lemmatizer.lemmatize(word) for word in document]
    document = [morph.normal_forms(word)[0] for word in document]
    tokenize_document.append(document)


In [82]:
token_text = [' '.join(i) for i in tokenize_document]
token_text

['москва музей отреставрировать ранний газ--универсал фото видео музей транспорт москва сообщить успешно завершить реставрация универсал газ - - год выпуск это самый ранний экземпляр модель сохраниться наш день газ - - — это грузопассажирский волга модификация такси отличие базовый модель - дефорсировать бензиновый мотор змз - л лс бензин - таксометр салон специальный световой прибор зелёный огонёк - го — фонарь крыша лимонный окраска кузов разметка шашечка буква так круг передний дверь машина полностью восстановить кузов салон двигатель коробка передача тормозной система рассказать директор музей оксана бондаренко салон газ - - — семь посадочный место компоновка + + передний аналогичный седан средний — оригинальный два сегмент широкий левый небольшой правый кресло третий ряд двухместный задний сидение складываться образовать ровный пол такой образ получить вместительный грузовой отсек грузоподъёмность волга — кг кресло модификация такси обтянутый дешёвый практичный кожзаменитель легко

In [83]:
#добавление в датафрейм обработанного текста 
data['token_text'] = token_text

#### Обучение на обработанных данных

In [ ]:
#tf = количество нашего слова в документе
#idf = ln[(1+количество документов)/(1+количество док-ов где встречается наше слово)]+1
#tf*idf
#потом происходит нормализация по евклидовой норме, idf/sqrt(Σtf**2) 

In [84]:
vectorizer = TfidfVectorizer(min_df = 10)
vectors = vectorizer.fit_transform(token_text)
fichi = pd.DataFrame(vectors.toarray(), columns=vectorizer.get_feature_names_out())
fichi

ab  actros   ag     aurus      auto  baic  benz   bm  bmw  bosch  \
0     0.000000     0.0  0.0  0.000000  0.000000   0.0   0.0  0.0  0.0    0.0   
1     0.000000     0.0  0.0  0.000000  0.000000   0.0   0.0  0.0  0.0    0.0   
2     0.074809     0.0  0.0  0.000000  0.000000   0.0   0.0  0.0  0.0    0.0   
3     0.000000     0.0  0.0  0.000000  0.069126   0.0   0.0  0.0  0.0    0.0   
4     0.000000     0.0  0.0  0.000000  0.000000   0.0   0.0  0.0  0.0    0.0   
...        ...     ...  ...       ...       ...   ...   ...  ...  ...    ...   
1093  0.000000     0.0  0.0  0.000000  0.000000   0.0   0.0  0.0  0.0    0.0   
1094  0.000000     0.0  0.0  0.000000  0.000000   0.0   0.0  0.0  0.0    0.0   
1095  0.000000     0.0  0.0  0.000000  0.000000   0.0   0.0  0.0  0.0    0.0   
1096  0.000000     0.0  0.0  0.000000  0.000000   0.0   0.0  0.0  0.0    0.0   
1097  0.000000     0.0  0.0  0.166637  0.000000   0.0   0.0  0.0  0.0    0.0   

      ...    юрлицо  являться      явно  язык  якобы       ямз  январь  \
0     ...  0.000000       0.0  0.000000   0.0    0.0  0.000000     0.0   
1     ...  0.000000       0.0  0.000000   0.0    0.0  0.109145     0.0   
2     ...  0.000000       0.0  0.000000   0.0    0.0  0.000000     0.0   
3     ...  0.069126       0.0  0.000000   0.0    0.0  0.000000     0.0   
4     ...  0.000000       0.0  0.000000   0.0    0.0  0.000000     0.0   
...   ...       ...       ...       ...   ...    ...       ...     ...   
1093  ...  0.000000       0.0  0.000000   0.0    0.0  0.000000     0.0   
1094  ...  0.000000       0.0  0.000000   0.0    0.0  0.000000     0.0   
1095  ...  0.000000       0.0  0.000000   0.0    0.0  0.000000     0.0   
1096  ...  0.000000       0.0  0.321472   0.0    0.0  0.000000     0.0   
1097  ...  0.000000       0.0  0.000000   0.0    0.0  0.000000     0.0   

      япония  японский  ёмкость  
0        0.0       0.0      0.0  
1        0.0       0.0      0.0  
2        0.0       0.0      0.0  
3        0.0       0.0      0.0  
4        0.0       0.0      0.0  
...      ...       ...      ...  
1093     0.0       0.0      0.0  
1094     0.0       0.0      0.0  
1095     0.0       0.0      0.0  
1096     0.0       0.0      0.0  
1097     0.0       0.0      0.0  

[1098 rows x 2183 columns]

In [85]:
data['комментарии']=data['комментарии'].fillna(data['комментарии'].median())

In [87]:
fichi['комментарии'] = data['комментарии']
y = data['лайки']

In [88]:
X_train, X_test, y_train, y_test = train_test_split(
fichi, y, test_size=0.3, random_state=42)

##### Выбор инструмента и подбор параметров

In [89]:
y.isnull().sum()

0

In [90]:
fichi

ab  actros   ag     aurus      auto  baic  benz   bm  bmw  bosch  \
0     0.000000     0.0  0.0  0.000000  0.000000   0.0   0.0  0.0  0.0    0.0   
1     0.000000     0.0  0.0  0.000000  0.000000   0.0   0.0  0.0  0.0    0.0   
2     0.074809     0.0  0.0  0.000000  0.000000   0.0   0.0  0.0  0.0    0.0   
3     0.000000     0.0  0.0  0.000000  0.069126   0.0   0.0  0.0  0.0    0.0   
4     0.000000     0.0  0.0  0.000000  0.000000   0.0   0.0  0.0  0.0    0.0   
...        ...     ...  ...       ...       ...   ...   ...  ...  ...    ...   
1093  0.000000     0.0  0.0  0.000000  0.000000   0.0   0.0  0.0  0.0    0.0   
1094  0.000000     0.0  0.0  0.000000  0.000000   0.0   0.0  0.0  0.0    0.0   
1095  0.000000     0.0  0.0  0.000000  0.000000   0.0   0.0  0.0  0.0    0.0   
1096  0.000000     0.0  0.0  0.000000  0.000000   0.0   0.0  0.0  0.0    0.0   
1097  0.000000     0.0  0.0  0.166637  0.000000   0.0   0.0  0.0  0.0    0.0   

      ...  являться      явно  язык  якобы       ямз  январь  япония  \
0     ...       0.0  0.000000   0.0    0.0  0.000000     0.0     0.0   
1     ...       0.0  0.000000   0.0    0.0  0.109145     0.0     0.0   
2     ...       0.0  0.000000   0.0    0.0  0.000000     0.0     0.0   
3     ...       0.0  0.000000   0.0    0.0  0.000000     0.0     0.0   
4     ...       0.0  0.000000   0.0    0.0  0.000000     0.0     0.0   
...   ...       ...       ...   ...    ...       ...     ...     ...   
1093  ...       0.0  0.000000   0.0    0.0  0.000000     0.0     0.0   
1094  ...       0.0  0.000000   0.0    0.0  0.000000     0.0     0.0   
1095  ...       0.0  0.000000   0.0    0.0  0.000000     0.0     0.0   
1096  ...       0.0  0.321472   0.0    0.0  0.000000     0.0     0.0   
1097  ...       0.0  0.000000   0.0    0.0  0.000000     0.0     0.0   

      японский  ёмкость  комментарии  
0          0.0      0.0          7.0  
1          0.0      0.0          3.0  
2          0.0      0.0         42.0  
3          0.0      0.0          1.0  
4          0.0      0.0          6.0  
...        ...      ...          ...  
1093       0.0      0.0          4.0  
1094       0.0      0.0          3.0  
1095       0.0      0.0          4.0  
1096       0.0      0.0          4.0  
1097       0.0      0.0         18.0  

[1098 rows x 2184 columns]

In [91]:
parametrs={'max_depth': [2,5,7,10],'n_estimators' : [10,50,100],'criterion':['squared_error'],'min_samples_split':[10,20,30],'min_samples_leaf':[10,20,30]}

regressor = RandomForestRegressor()

#### Обучение модели 

In [92]:
grid_search_cv_reg=GridSearchCV(regressor, parametrs, cv=5)#добавляем еще кросс-валидацию с пятью фолдами
grid_search_cv_reg.fit(X_train, y_train)
best_reg = grid_search_cv_reg.best_estimator_

In [93]:
grid_search_cv_reg.best_params_#лучшие параметры для нашей модели

{'criterion': 'squared_error',
 'max_depth': 10,
 'min_samples_leaf': 10,
 'min_samples_split': 10,
 'n_estimators': 100}

#### Глубина дерева равна 10 при подборе параметров, это нормально так как чтобы не было переобучения применяется кросс-валидация (тренировочные данные разбиваются на 5 фолдов)

#### Обучение на оригинальных данных

In [99]:
tknzr = TweetTokenizer()
original_document = []

for document in data['посты']:
    document = tknzr.tokenize(document)
    document = [word.lower() for word in document]
    original_document.append(document)

In [100]:
original_text = [' '.join(i) for i in original_document]
original_text

['в москве музей отреставрировал ранний газ - 24 - универсал ( фото , видео ) музей транспорта москвы сообщил , что успешно завершил реставрацию универсала газ -24-04 1972 года выпуска , то есть это один из самых ранних экземпляров модели , сохранившихся до наших дней . газ -24-04 — это грузопассажирская волга в модификации для такси . отличия от базовой модели 24-02 : дефорсированный бензиновый мотор змз - 2401 ( 2,5 л , 75 л . с . , бензин а - 76 ) , таксометр в салоне , специальные световые приборы ( « зеленый огонек » , а с 1980 - го — фонарь на крыше ) , лимонная окраска кузова и разметка « шашечками » с буквой т в круге на передних дверях . машине полностью восстановили кузов , салон , двигатель , коробку передач и тормозную систему , рассказала директор музея оксана бондаренко . в салоне газ -24-04 — семь посадочных мест , компоновка 2 + 3 + 2 . передние аналогичны седану , среднее — оригинальное из двух сегментов ( более широкого левого и небольшого правого ) , кресло третьего 

In [101]:
#добавление в датафрейм обработанного текста 
data['original_text'] = original_text

In [102]:
vectorizer = TfidfVectorizer(min_df = 10)
vectors = vectorizer.fit_transform(original_text)
fichi = pd.DataFrame(vectors.toarray(), columns=vectorizer.get_feature_names_out())
fichi

000   10       100  1000  106   11  110  116   12       120  ...  юрий  \
0     0.0  0.0  0.000000   0.0  0.0  0.0  0.0  0.0  0.0  0.000000  ...   0.0   
1     0.0  0.0  0.000000   0.0  0.0  0.0  0.0  0.0  0.0  0.000000  ...   0.0   
2     0.0  0.0  0.093682   0.0  0.0  0.0  0.0  0.0  0.0  0.067103  ...   0.0   
3     0.0  0.0  0.000000   0.0  0.0  0.0  0.0  0.0  0.0  0.000000  ...   0.0   
4     0.0  0.0  0.000000   0.0  0.0  0.0  0.0  0.0  0.0  0.000000  ...   0.0   
...   ...  ...       ...   ...  ...  ...  ...  ...  ...       ...  ...   ...   
1093  0.0  0.0  0.000000   0.0  0.0  0.0  0.0  0.0  0.0  0.000000  ...   0.0   
1094  0.0  0.0  0.000000   0.0  0.0  0.0  0.0  0.0  0.0  0.000000  ...   0.0   
1095  0.0  0.0  0.000000   0.0  0.0  0.0  0.0  0.0  0.0  0.000000  ...   0.0   
1096  0.0  0.0  0.000000   0.0  0.0  0.0  0.0  0.0  0.0  0.000000  ...   0.0   
1097  0.0  0.0  0.049439   0.0  0.0  0.0  0.0  0.0  0.0  0.000000  ...   0.0   

        юрлицо  является  являются      явно  якобы       ямз  январе  января  \
0     0.000000       0.0       0.0  0.000000    0.0  0.000000     0.0     0.0   
1     0.000000       0.0       0.0  0.000000    0.0  0.116575     0.0     0.0   
2     0.000000       0.0       0.0  0.000000    0.0  0.000000     0.0     0.0   
3     0.076127       0.0       0.0  0.000000    0.0  0.000000     0.0     0.0   
4     0.000000       0.0       0.0  0.000000    0.0  0.000000     0.0     0.0   
...        ...       ...       ...       ...    ...       ...     ...     ...   
1093  0.000000       0.0       0.0  0.000000    0.0  0.000000     0.0     0.0   
1094  0.000000       0.0       0.0  0.000000    0.0  0.000000     0.0     0.0   
1095  0.000000       0.0       0.0  0.000000    0.0  0.000000     0.0     0.0   
1096  0.000000       0.0       0.0  0.248023    0.0  0.000000     0.0     0.0   
1097  0.000000       0.0       0.0  0.000000    0.0  0.000000     0.0     0.0   

      японии  
0        0.0  
1        0.0  
2        0.0  
3        0.0  
4        0.0  
...      ...  
1093     0.0  
1094     0.0  
1095     0.0  
1096     0.0  
1097     0.0  

[1098 rows x 2664 columns]

In [103]:
fichi['комментарии'] = data['комментарии']
y = data['лайки']

In [104]:
X_train_orig, X_test_orig, y_train_orig, y_test_orig = train_test_split(
fichi, y, test_size=0.3, random_state=42)

In [105]:
grid_search_cv_reg=GridSearchCV(regressor, parametrs, cv=5)#добавляем еще кросс-валидацию с пятью фолдами
grid_search_cv_reg.fit(X_train_orig, y_train_orig)
best_reg_original = grid_search_cv_reg.best_estimator_

#### Метрики на обработанных данных

#### На тренировочных данных

In [94]:
from sklearn.metrics import mean_squared_error
from sklearn.metrics import mean_absolute_error

print(f"MSE = {mean_squared_error(y_train,best_reg.predict(X_train))}")
print(f"MAE = {mean_absolute_error(y_train,best_reg.predict(X_train))}")

MSE = 3488.7957987644863
MAE = 38.36985711318327


#### На тестовых данных

In [98]:
from sklearn.metrics import mean_squared_error
from sklearn.metrics import mean_absolute_error

print(f"MSE = {mean_squared_error(y_test,best_reg.predict(X_test))}")
print(f"MAE = {mean_absolute_error(y_test,best_reg.predict(X_test))}")

MSE = 3997.492587892497
MAE = 43.49676710617256


#### Метрики на оригинальных данных

#### На тренировочных данных

In [106]:
from sklearn.metrics import mean_squared_error
from sklearn.metrics import mean_absolute_error

print(f"MSE = {mean_squared_error(y_train_orig,best_reg_original.predict(X_train_orig))}")
print(f"MAE = {mean_absolute_error(y_train_orig,best_reg_original.predict(X_train_orig))}")

MSE = 3555.800837512513
MAE = 38.33193139628437


#### На тестовых данных

In [111]:
from sklearn.metrics import mean_squared_error
from sklearn.metrics import mean_absolute_error

print(f"MSE = {mean_squared_error(y_test_orig,best_reg_original.predict(X_test_orig))}")
print(f"MAE = {mean_absolute_error(y_test_orig,best_reg_original.predict(X_test_orig))}")

MSE = 4068.3091889706398
MAE = 43.91605367529316
